In [150]:
%pylab inline

Populating the interactive namespace from numpy and matplotlib


In [1]:
import dataiku
from dataiku import pandasutils as pdu
import pandas as pd
import re
import tensorflow
from tensorflow.keras.preprocessing.text import Tokenizer

In [2]:
#df=pd.read_csv("/NAMESCREENING_1/X71uZTip/Processed_Names.csv")
import os
# Recipe inputs
folder_path = dataiku.Folder("X71uZTip").get_path()  #/* FuShmlsH is the Folder ID */
path_of_csv = os.path.join(folder_path, "Processed_Names.csv") #/* dataset_01.csv is one of the files in this folder */
df=pd.read_csv(path_of_csv)

In [0]:
df

In [3]:
print(df["ALL_ALIAS_NAMES"].apply(lambda x : type(x)).unique())
print(df["ALL_PARTY_NAMES"].apply(lambda x: type(x)).unique())
print(df["ALL_WL_NAMES"].apply(lambda x: type(x)).unique())

[<class 'str'>]
[<class 'str'>]
[<class 'str'>]


In [4]:
df["ALL_WL_NAMES"]

0         ['', '', '', '', '', '', 'SHARUDDIN BIN MD SAL...
1                 ['', '', '', '', '', '', 'HO KIONG CHAN']
2         ['', '', '', '', '', '', 'AHMAD ASABI BIN ISMA...
3                   ['', '', '', '', '', '', 'ANG LEE ENG']
4                   ['', '', '', '', '', '', 'ANG LEE ENG']
                                ...                        
829278           ['', '', '', '', '', '', 'MUHAMMAD UMAIR']
829279           ['', '', '', '', '', '', 'MUHAMMAD UMAIR']
829280           ['', '', '', '', '', '', 'MUHAMMAD UMAIR']
829281            ['', '', '', '', '', '', 'MARIKO SUZUKI']
829282    ['LIU YUAN YUAN', '', '', '', '', '', 'YUANYUA...
Name: ALL_WL_NAMES, Length: 829283, dtype: object

In [6]:
# need to remove brackets & split based on comma as whole input ius complete one string.
list_col=["ALL_ALIAS_NAMES","ALL_PARTY_NAMES","ALL_WL_NAMES"]
def str_gen(col_nam):
    df[col_nam]=df[col_nam].apply(lambda x: x.lstrip("[").rstrip("]"))
    df[col_nam]=df[col_nam].apply(lambda x : re.split(",",x))
    df[col_nam]=df[col_nam].apply(lambda x: [i.strip("\"").strip(' \'') for i in x])

for i in list_col:
    str_gen(i)

In [7]:
df["ALL_WL_NAMES"]

0           [, , , , , , SHARUDDIN BIN MD SALLEH]
1                     [, , , , , , HO KIONG CHAN]
2            [, , , , , , AHMAD ASABI BIN ISMAIL]
3                       [, , , , , , ANG LEE ENG]
4                       [, , , , , , ANG LEE ENG]
                           ...                   
829278               [, , , , , , MUHAMMAD UMAIR]
829279               [, , , , , , MUHAMMAD UMAIR]
829280               [, , , , , , MUHAMMAD UMAIR]
829281                [, , , , , , MARIKO SUZUKI]
829282    [LIU YUAN YUAN, , , , , , YUANYUAN LIU]
Name: ALL_WL_NAMES, Length: 829283, dtype: object

In [8]:
print(df["ALL_ALIAS_NAMES"].apply(lambda x: type(x)).unique())
print(df["ALL_PARTY_NAMES"].apply(lambda x: type(x)).unique())
print(df["ALL_WL_NAMES"].apply(lambda x: type(x)).unique())


[<class 'list'>]
[<class 'list'>]
[<class 'list'>]


# Filtering alerts with resolution TH , THNM and comments have match names.

In [12]:
# case-1 comments with name match but may have or not name variations
'''
print(df[df["V_COMMENTSs"].str.contains("Match Full Legal Name|Match Name|Match_ Full Legal Name|Match name|Match_name|Matched Name|Matched name\
Match_Name|Match_Full Legal Name")][["v_comments","v_regd_party_name","v_profile_name","v_resolution"]])


# case -2 comments with name match but have having name variations

print("alerts closed with TH resolution having name match as comments but having name variation", \
     df[(df["V_COMMENTS"].str.contains("Match Full Legal Name|Match Name|Match_ Full Legal Name|Match name|Match_name|Matched Name|Matched name\
Match_Name|Match_Full Legal Name") )& (df["v_regd_party_name"]!=df["v_profile_name"])][["v_comments","v_regd_party_name","v_profile_name"]].shape)
'''


'\nprint(df[df["V_COMMENTSs"].str.contains("Match Full Legal Name|Match Name|Match_ Full Legal Name|Match name|Match_name|Matched Name|Matched nameMatch_Name|Match_Full Legal Name")][["v_comments","v_regd_party_name","v_profile_name","v_resolution"]])\n\n\n# case -2 comments with name match but have having name variations\n\nprint("alerts closed with TH resolution having name match as comments but having name variation",      df[(df["V_COMMENTS"].str.contains("Match Full Legal Name|Match Name|Match_ Full Legal Name|Match name|Match_name|Matched Name|Matched nameMatch_Name|Match_Full Legal Name") )& (df["v_regd_party_name"]!=df["v_profile_name"])][["v_comments","v_regd_party_name","v_profile_name"]].shape)\n'

In [10]:
df["V_COMMENTS"]=df["V_COMMENTS"].apply(lambda x: "" if pd.isna(x) else x)
# We assume that all the alerts that are close because of names anchor should have name as text in comments .Now secondly, 
# we need to check that when commenst contain name as string , whether the context of comment is alogned with resolution TH , THNM, FP.
# So we obtain value counts for TH, THNM & FP .Now check with existing observed comments like Match Full leagal name , to see what extent to we approach to these value counts.
patt=re.compile("name",re.IGNORECASE)
print(df[df["V_COMMENTS"].str.contains(patt,re.IGNORECASE)].shape)
print(df[df["V_COMMENTS"].str.contains(patt,re.IGNORECASE)]["V_RESOLUTION"].value_counts())


patt_2=re.compile("Match Full Legal Name|Match Name|Match_ Full Legal Name|Match name|Match_name|Matched Name|Matched name\
Match_Name|Match_Full Legal Name|Match ID and Full Legal Name|Match ID or Full Legal Name|Match ID & Legal Name|Match ID and/or Full Legal Name|Match_ Name|Match Full Legal  Name",re.IGNORECASE)

df_TH_comm_val=pd.DataFrame({})
df_TH_comm_val=df[(df["V_COMMENTS"].str.contains(patt_2)) & (df["V_RESOLUTION"].isin(["TH","THNM"]))]

print(df[(df["V_COMMENTS"].str.contains(patt_2)) & (df["V_RESOLUTION"].isin(["TH","THNM"]))].shape)

(196799, 7)
FP      127755
TH       67294
THNM      1741
RW           9
Name: V_RESOLUTION, dtype: int64
(64061, 7)


We see that out of 69,035 alerts with comments as name & resolution TH, THNM we are able to validate for 64061.Refer jupyter noreboook Comment_Analysis_For_Names to see the alerts where comments cannot be validated.

# Filtering the alerts with resolution as FP and comments as name miss-match


In [76]:
df[(df["V_COMMENTS"].str.contains(patt)) & (df["V_RESOLUTION"]=="FP")].shape

(127755, 7)

In [13]:
# We need to check whether the context in which name is coming in comments is aligned with resolution FP.So we have existing 
# comments based on which we validate that upto how much alerts with name in comments & FP can we achieve.
patt_3=re.compile("Mismatch Full Legal Name|not sounds similar|not sound similar",re.IGNORECASE)
print(df[(df["V_COMMENTS"].str.contains(patt_3)) & (df["V_RESOLUTION"]=="FP")]["V_COMMENTS"].shape)
# Refer Comment_Analysis_For_Names to see the alerts where commenst could not be validated i.e 14 thousand alerts approx.

df_FP_comm_val=df[(df["V_COMMENTS"].str.contains(patt_3)) & (df["V_RESOLUTION"]=="FP")]

(113055,)


In [14]:
print(df_TH_comm_val.shape[0]+df_FP_comm_val.shape[0])
df_comm_val=pd.concat([df_TH_comm_val,df_FP_comm_val],axis=0,join="outer")
df_comm_val = df_comm_val.sample(frac=1, random_state=42).reset_index(drop=True)
df_comm_val.head()

177116


Unnamed: 0                   ALL_ALIAS_NAMES                           ALL_PARTY_NAMES                                       ALL_WL_NAMES                                         V_COMMENTS V_RESOLUTION  N_MATCH_SCORE
0      270848  [, , , , , , , , , , , , , , , ]        [ABDUL AZIZ BIN ABDUL TALIB, , , ]  [ABDUL AZIZ ABDUL HALIM, , , , , , ABDUL HALIM...           Mismatch Full Legal Name_Name Structure            FP           91.0
1      746714  [, , , , , , , , , , , , , , , ]  [MOHD SHAH SAIFUL RIZZA BIN JASRI, , , ]     [, , , , , , MOHD SHAH SAIFUL RIZZA BIN JASRI]  Match Name, Gender, Nationality, Date of Birth...           TH          100.0
2      648910  [, , , , , , , , , , , , , , , ]                       [YOW AI NGOH, , , ]                          [, , , , , , YOW AI NGOH]                  Match ID and/or Full Legal Name\n           TH          100.0
3      659513  [, , , , , , , , , , , , , , , ]    [NUR NAZIHAH NABIHAH ABDUL ZIZI, , , ]       [, , , , , , NUR NAZIHAH NABIHAH ABDUL ZIZI]                    Match ID and/or Full Legal Name           TH          100.0
4      794331  [, , , , , , , , , , , , , , , ]                      [YANG CHUNLIN, , , ]            [YANG CHUN YIN, , , , , , CHUNYIN YANG]  Mismatch Full Legal Name_Name does not sound s...           FP           92.0

In [92]:
def similarity_score(x,y):
    

Unnamed: 0                                    ALL_ALIAS_NAMES                                   ALL_PARTY_NAMES                                       ALL_WL_NAMES                                         V_COMMENTS V_RESOLUTION  N_MATCH_SCORE
270848      270848  ['', '', '', '', '', '', '', '', '', '', '', '...        ['ABDUL AZIZ BIN ABDUL TALIB', '', '', '']  ['ABDUL AZIZ ABDUL HALIM', '', '', '', '', '',...           Mismatch Full Legal Name_Name Structure            FP           91.0
746714      746714  ['', '', '', '', '', '', '', '', '', '', '', '...  ['MOHD SHAH SAIFUL RIZZA BIN JASRI', '', '', '']  ['', '', '', '', '', '', 'MOHD SHAH SAIFUL RIZ...  Match Name, Gender, Nationality, Date of Birth...           TH          100.0
648910      648910  ['', '', '', '', '', '', '', '', '', '', '', '...                       ['YOW AI NGOH', '', '', '']            ['', '', '', '', '', '', 'YOW AI NGOH']                  Match ID and/or Full Legal Name\n           TH          100.0
659513      659513  ['', '', '', '', '', '', '', '', '', '', '', '...    ['NUR NAZIHAH NABIHAH ABDUL ZIZI', '', '', '']  ['', '', '', '', '', '', 'NUR NAZIHAH NABIHAH ...                    Match ID and/or Full Legal Name           TH          100.0
794331      794331  ['', '', '', '', '', '', '', '', '', '', '', '...                      ['YANG CHUNLIN', '', '', '']  ['YANG CHUN YIN', '', '', '', '', '', 'CHUNYIN...  Mismatch Full Legal Name_Name does not sound s...           FP           92.0
...            ...                                                ...                                               ...                                                ...                                                ...          ...            ...
417566      417566  ['', '', '', '', '', '', '', '', '', '', '', '...         ['MOHD ROHAFIZ BIN ABDULLAH', '', '', '']  ['', '', '', '', '', '', 'MOHAMMAD HAFIZ BIN A...  Mismatch ID number_NRIC, DOB & Full Legal Name...           FP           91.0
295972      295972  ['', '', '', '', '', '', '', '', '', '', '', '...                      ['TAN ENG HONG', '', '', '']          ['', '', '', '', '', '', 'TAN KENG HONG']  Mismatch Full Legal Name_Name Does Not Sound S...           FP           93.0
507509      507509  ['', '', '', '', '', '', '', '', '', '', '', '...                       ['ZAW LIN TUN', '', '', '']  ['ZAW MIN', 'ZAW MIN TUN', 'ZAW MIN TUN', '', ...  Mismatch Full Legal Name_ Name Does Not Sound ...           FP           91.0
606297      606297  ['', '', '', '', '', '', '', '', '', '', '', '...                     ['LI   JINXIANG', '', '', '']  ['LI JING XIANG', '', '', '', '', '', 'JINGXIA...  Mismatch Full Legal Name_Chinese Native Charac...           FP           92.0
432509      432509  ['', '', '', '', '', '', '', '', '', '', '', '...                  ['NORAIN ABU BAKAR', '', '', '']      ['', '', '', '', '', '', 'NORAINI ABU BAKAR']  Mismatch Full Legal Name_Name does not sound s...           FP           95.0

[177116 rows x 7 columns]

    Tokenizing 
    Text to Sequence
    Siamese Architechture
    Training & Call backs
    Graphical Analysis
    Random Search & Bayesian Optimization
    Best model
    Model prediction


### Tokenization

In [0]:
pd.set_options()

In [15]:
df_comm_val["ALL_WL_NAMES"].values

array([list(['ABDUL AZIZ ABDUL HALIM', '', '', '', '', '', 'ABDUL HALIM BIN ABDUL AZIZ']),
       list(['', '', '', '', '', '', 'MOHD SHAH SAIFUL RIZZA BIN JASRI']),
       list(['', '', '', '', '', '', 'YOW AI NGOH']), ...,
       list(['ZAW MIN', 'ZAW MIN TUN', 'ZAW MIN TUN', '', '', '', '', '', '', '', '', '', '', '', 'ZAW MIN TUN']),
       list(['LI JING XIANG', '', '', '', '', '', 'JINGXIANG LI']),
       list(['', '', '', '', '', '', 'NORAINI ABU BAKAR'])], dtype=object)

In [20]:
col_val=[]
for i in df_comm_val[col_nam].values:
    col_val=col_val + list(set(i))

In [21]:
col_val

['',
 'ABDUL AZIZ BIN ABDUL TALIB',
 '',
 'MOHD SHAH SAIFUL RIZZA BIN JASRI',
 '',
 'YOW AI NGOH',
 '',
 'NUR NAZIHAH NABIHAH ABDUL ZIZI',
 '',
 'YANG CHUNLIN',
 '',
 'CHIN WAI LEONG',
 'ABDUL RAHMAN BIN ABDULLAH',
 '',
 '',
 'ZURINA OTHMAN',
 '',
 'ABD RAHIM BIN ABDUL WAHID',
 '',
 'KOH AIK HEAN',
 '',
 'GANESAN ANTHONYSAMY',
 '',
 'SITI AMINAH ABDUL RAHMAN',
 '',
 'WONG KONG CHAN',
 '',
 'ZALINA OTHMAN',
 '',
 'NORAINI IDRIS',
 '',
 'SITI NURHIKMAH ABDULLAH',
 'ABDUL HARIS BIN ZAKARIA',
 '',
 '',
 'TAN CHEN HONG',
 '',
 'ZHANG YING',
 '',
 'SILVARAJU M NADARAJAN',
 'RISIMAH',
 '',
 'MUHAMMAD NOOR BIN JANTAN',
 '',
 '',
 'GU WEN',
 '',
 'SAMANEH AMIRISOORI',
 '',
 'JASBINDER SINGH KIRPAL SINGH',
 'LIBIN ZHAO',
 '',
 '',
 'IBRAHIM BIN MOHD HASHIM',
 '',
 'CHUA CHIN YAW',
 '',
 'ZHANG RONGRONG',
 '',
 'MUHAMMAD SYAMIR BIN MOKHTAR',
 '',
 'ABDUL HAKIM',
 '',
 'ABDUL HALIM BIN ABU BAKAR',
 '',
 'ZURAIDAH ABDUL AZIZ',
 '',
 'MIN MIN TUN',
 '',
 'ZHANG QUN',
 '',
 'MOHD RAZAIMIE BIN ABDUL R

In [26]:
%%time
l=["ALL_PARTY_NAMES","ALL_ALIAS_NAMES","ALL_WL_NAMES"]
cust_wl_names=[]
col_val=[]
for col_nam in l:
    col_val=col_val+[list(set(i)) for i in df_comm_val[col_nam]]
'''
    for i in col_val:
    cust_wl_names=cust_wl_names+i
#    cust_wl_names=cust_wl_names+col_val
    
cust_wl_names
'''

CPU times: user 1.64 s, sys: 260 ms, total: 1.89 s
Wall time: 1.89 s


'\n    for i in col_val:\n    cust_wl_names=cust_wl_names+i\n#    cust_wl_names=cust_wl_names+col_val\n    \ncust_wl_names\n'

In [28]:
for i in col_val:
    cust_wl_names=cust_wl_names+i

In [117]:
len(cust_wl_names)

7

In [106]:
cust_wl_names=list(set(df_comm_val["ALL_PARTY_NAMES"].tolist()+df["ALL_PROFILE_NAMES"].tolist()+df["ALL_WL_NAMES"].tolist()))

KeyError: 'ALL_PROFILE_NAMES'

In [107]:
# Tokenizer - it means generating index for each token ( can be word or character) . So we need unique set of tokens


def tokenize(x,y):
    cust_wl_names=list(set(df["ALL_PARTY_NAMES"].tolist()+df["ALL_PROFILE_NAMES"].tolist()+df["ALL_WL_NAMES"].tolist()))
    


cust_and_wl_names = list(set(df['V_REGD_PARTY_NAME'].tolist()+\
                               df['V_WATCHLIST_PARTY_NAME'].tolist())) # list of list of unique set of names present in customer & watchlist data

#cust_and_wl_names=names_and_nicknames[1:] # we obtain character level tokenization since char_level is true.
tk = Tokenizer(num_words=None, char_level=True, oov_token='UNK') # creating object of class tokenizer
tk.fit_on_texts(cust_and_wl_names)                              
#print(f"There are {len(tk.word_index)} unique tokens in Train+Val+Test sets.")
tk.word_index

length = []

for i in range(len(cust_and_wl_names)):
    length.append(len(cust_and_wl_names[i]))
    
print(max(length))









70


In [108]:
tk.word_index.values()

dict_values([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29])

In [109]:
tk.word_index
for j,i in enumerate(cust_and_wl_names):
    if '\xa0' in i:
         print(j,i)

1906 ZULKIFLI BIN MOHD NOORA A A A A A A A A A A A A A A A A A A 
3686 NORMIMAH NONGCHIA A A A A A A A A A A A A A A A A A A A A A A A A A A 
6047 SHIV NARAYAN CHAUDHARYA A A A A A A A A A A A A A A A A A A A A 
7557 EZRYLA RASYDANA BINA OMAR
41851 MUHAMMAD IBRAHIM BIN ABDULLAHA 


In [110]:


# construct a new vocabulary 
# --------------------

# alphabet="abcdefghijklmnopqrstuvwxyz0123456789-,;.!?:'\"/\|_@#$%^&*~`+-=<>()[]{}"
alphabet=''.join(list(tk.word_index.keys())).replace('UNK','')
#print('Alphabet')
#print(alphabet)
#print('')

char_dict = {}
for i, char in enumerate(alphabet):
    char_dict[char] = i + 1
    
# Use char_dict to replace the tk.word_index
tk.word_index = char_dict 
# Add 'UNK' to the vocabulary 
tk.word_index[tk.oov_token] = max(char_dict.values()) + 1




In [111]:
del char_dict["\xa0"]
char_dict["UNK"]=28
char_dict

{'a': 1,
 ' ': 2,
 'i': 3,
 'n': 4,
 'h': 5,
 'm': 6,
 'o': 7,
 'd': 8,
 'b': 9,
 'l': 10,
 'u': 11,
 'e': 12,
 'r': 13,
 's': 14,
 'g': 15,
 'k': 16,
 'z': 17,
 't': 18,
 'y': 19,
 'f': 20,
 'c': 21,
 'w': 22,
 'j': 23,
 'p': 24,
 'v': 25,
 'q': 26,
 'x': 27,
 'UNK': 28}

In [112]:
np.max(df['V_WATCHLIST_PARTY_NAME'])

'ZURYIANTI'

In [113]:
max(3,5)

5

In [114]:
input_dim=len(char_dict.keys())

In [115]:
# change 1 - add "x"
tk

In [116]:
# convert names into sequences

### turning into Sequences & Padding

from tensorflow.keras.utils import pad_sequences
# -------------------
maxlen = max([51,len(np.max(df['V_REGD_PARTY_NAME'])),len(np.max(df['V_WATCHLIST_PARTY_NAME']))])

sequences_names_cust = tk.texts_to_sequences(df['V_REGD_PARTY_NAME'].tolist())
sequences_names_wl = tk.texts_to_sequences(df['V_WATCHLIST_PARTY_NAME'].tolist())


# Padding to 51
cust_pad_names = pad_sequences(sequences_names_cust, maxlen=maxlen, padding='post')
wl_pad_names = pad_sequences(sequences_names_wl, maxlen=maxlen, padding='post')




In [117]:
cust_pad_names

array([[ 6,  7, 23, ...,  0,  0,  0],
       [ 5,  1, 10, ...,  0,  0,  0],
       [ 5,  1,  6, ...,  0,  0,  0],
       ...,
       [ 1, 17,  1, ...,  0,  0,  0],
       [ 4, 11, 13, ...,  0,  0,  0],
       [23,  1, 14, ...,  0,  0,  0]], dtype=int32)

In [118]:
# Convert to numpy array
cust_pad_names = np.array(cust_pad_names)
wl_pad_names = np.array(wl_pad_names)

print(df['V_REGD_PARTY_NAME'].tolist()[1])
print(cust_pad_names [1])

HALA ASSAF
[ 5  1 10  1  2  1 14 14  1 20  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
  0  0  0]


In [90]:
l_1=df[df["label"]==1]
l_0=df[df["label"]==0]

In [91]:
l_1["label"].replace(to_replace={1:0},inplace=True)
l_0["label"].replace(to_replace={0:1},inplace=True)


/app/dataiku/design/code-envs/python/py_39_tm_ns/lib/python3.9/site-packages/pandas/core/series.py:4576: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().replace(


In [92]:
df=pd.concat([l_1,l_0],axis=0).reset_index(drop=True)

In [94]:
df.shape

(83007, 3)

In [96]:
df.shape

(83007, 3)

In [0]:
df
#df=df.iloc[:,:3]

In [90]:
l_1=df[df["label"]==1]
l_0=df[df["label"]==0]

In [91]:
l_1["label"].replace(to_replace={1:0},inplace=True)
l_0["label"].replace(to_replace={0:1},inplace=True)


/app/dataiku/design/code-envs/python/py_39_tm_ns/lib/python3.9/site-packages/pandas/core/series.py:4576: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().replace(


In [92]:
df=pd.concat([l_1,l_0],axis=0).reset_index(drop=True)

In [93]:
df.head()

V_WATCHLIST_PARTY_NAME              V_REGD_PARTY_NAME  label
0            MOJTABA SOLTANI ALI            MOJTABA SOLTANI ALI      0
1                     HALA ASSAF                     HALA ASSAF      0
2  HAMZA AL KOUZBARY AHMAD RATEB  HAMZA AL KOUZBARY AHMAD RATEB      0
3                Shivakumar NAIR                SHIVAKUMAR NAIR      0
4                RAGHDAA ALBAYAT                RAGHDAA ALBAYAT      0

In [94]:
df.shape

(83007, 3)

In [95]:
df[df.duplicated(subset=["V_WATCHLIST_PARTY_NAME","V_REGD_PARTY_NAME","label"])]

V_WATCHLIST_PARTY_NAME                        V_REGD_PARTY_NAME  label
25122                                           Abdullah Bin ABD RAHMAN                ABDUL RAHMAN BIN ABDULLAH      1
25135                                      Abdul Halim Bin ABDUL RAHMAN             ABDUL RAHMAN BIN ABDUL HAMID      1
25152                                           Abdullah Bin ABD RAHMAN                ABDUL RAHMAN BIN ABDULLAH      1
25159                                          Abdul Rahman ABDUL HAMID                   AB HALIM BIN AB RAHMAN      1
25248                                             Rahman Bin ABD RAHMAN                   ABDUL RAHMAN BIN AHMAD      1
25274                                                       Ahmed AYMAN                          AZMAN BIN AHMAD      1
25294                                                 Ahmad Bin IBRAHIM                        IBRAHIM BIN AHMAD      1
25299                                 Tengku Azizah Binti TENGKU HASSAN                      AZIZAH BINTI HASSAN      1
25310                                                       Ahmed AYMAN                          AZMAN BIN AHMAD      1
25313                                                 Ahmad Bin IBRAHIM                        IBRAHIM BIN AHMAD      1
25321                                               Khairin Nisa ISMAIL                 KHAIRUNNISA BINTI ISMAIL      1
25329                                             Rahman Bin ABD RAHMAN                   ABDUL RAHMAN BIN AHMAD      1
25369                                           Zainol Abidin Bin AHMAD                  ZAINAL ABIDIN BIN AHMAD      1
25407                                           Abdullah Bin ABD RAHMAN                ABDUL RAHMAN BIN ABDULLAH      1
25424                                                      NAY WIN AUNG                             NAY LIN AUNG      1
25444                                                     Hock Keng TAN                            TAN SENG HOCK      1
25488                                              Abdullah ABDUL HAMID                 ABDUL HALIM BIN ABDULLAH      1
25524                                                    Maslina ISMAIL                     MASLIZA BINTI ISMAIL      1
25527                                              Salinah Binti ISMAIL                     SAKINAH BINTI ISMAIL      1
25538                                 Tengku Azizah Binti TENGKU HASSAN                      AZIZAH BINTI HASSAN      1
25550                                      Abdul Halim Bin ABDUL RAHMAN             ABDUL RAHMAN BIN ABDUL HAMID      1
25555                                                Ismail Bin ZAKARIA                       ZAKARIA BIN ISMAIL      1
25558                                           Zainol Abidin Bin AHMAD                  ZAINAL ABIDIN BIN AHMAD      1
25589                                           Abdul Halim Bin HUSSAIN                     ABD HALIM BIN HASSAN      1
25597                                             Rahman Bin ABD RAHMAN                     ABD RAHMAN BIN AHMAD      1
25618                                                       Nazul ISLAM                              TAZUL ISLAM      1
25620                                             Rahman Bin ABD RAHMAN                   ABDUL RAHMAN BIN AHMAD      1
25626                                             Muhammad Bin ABDULLAH                     ABDULLAH BIN MUHAMAD      1
25658                                                 Mohamad Abd RAZAK                  ABDUL RAZAK BIN MOHAMED      1
25667                                            Mohd Azmi Bin MOHD ALI               MOHAMAD AFIQ BIN MOHD AZMI      1
25670                                                     BONG CHEE WEI                             ONG CHEE WEI      1
25694                                                      Shukri AHMAD                    AHMAD SUKRI BIN AWANG      1
25701                                                 Rozina ABD RAHMAN                  

In [96]:
df.shape

(83007, 3)